## Neural Network NER

In [1]:
import numpy as np
from os import listdir
import pickle
from xml.dom.minidom import parse
import matplotlib.pyplot as plt
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

from tensorflow.keras.optimizers import Adam
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import load_model
from keras.models import Model, Input
from keras.layers import *

stopwords = set(stopwords.words("english"))
from evaluator import *

%matplotlib inline

## Functions Learner

In [2]:
def find_multi_token_entity(ents, token):
    keys = ents.keys()
    for k in keys:
        if token in k:
            return ents[k]

def load_data(datadir):
    '''
    Task: Load XML files in given directory, tokenize each sentence, and extract
    ground truth BIO labels for each token.
    
    Input: 
        datadir: A directory containing XML files
        
    Output: A directory containing the dataset. Dictionary key is sentence_id, and the 
            value is a list of token tuples (word, start, end, ground truth).
            
    Example: 
            >>> load_data('data/Train')
            {'DDI-DrugBank.d370.s0': [('as', 0, 1,'O'), ('differin', 3, 10,'B-brand'),
                     ('gel', 12, 14,'O'), ... , ('with', 343, 346, 'O'),
                     ('caution', 348, 354, 'O'), ('.', 355, 355, 'O')],
            'DDI-DrugBank.d370.s1': [('particular', 0, 9, 'O'), ('caution', 11, 17, 'O'),
                     ('should', 19, 24, 'O'), ... , ('differin', 130, 137, 'B-brand'),
                     ('gel', 139, 141, 'O'), ('.', 142, 142, 'O')], ... }
    '''
    
    dict_dataset = {}
    
    for f in listdir(datadir):
        tree = parse(datadir + "/" + f)
        
        sentences = tree.getElementsByTagName("sentence")
        for s in sentences: 
            sid = s.attributes["id"].value
            
            stext = s.attributes["text"].value
            #stext = stext.replace("-"," ") if used we lose beta-endorphin, if not use we lose calcium-rich tag
            
            ents = {}
            entities = s.getElementsByTagName("entity")
            for e in entities:
                offset = e.attributes["charOffset"].value
                offsets = offset.split(';')
                name = e.attributes["text"].value
                e_type = e.attributes["type"].value
                ents[name] = {"type": e_type, "offsets": []}
                for offset in offsets:
                    start = offset.split('-')[0]
                    end = offset.split('-')[1]
                    ents[name]["offsets"].append((start, end))
            
            punct = [",",";",":","?","!", "(", ")"] # removed "."
            tokens = word_tokenize(stext)
            tokens_cleaned = []
            for t in tokens:
                if t not in punct and t not in stopwords:
                    tokens_cleaned.append(t)
            
            tags = []
            tokens = []
            for t in tokens_cleaned:
                offsetFrom = stext.find(t)
                offsetTo = offsetFrom + len(t) - 1
                # 1-token entities
                if t in ents:
                    if (int(ents[t]["offsets"][0][0]) == offsetFrom):
                        tag = "B-"+ents[t]["type"] # TODO: ents after .?
                    else:
                        tag = "I-"+ents[t]["type"]                    
                else:
                    multi_token_ent = find_multi_token_entity(ents, t)
                    if multi_token_ent:
                        if (int(multi_token_ent["offsets"][0][0]) == offsetFrom):
                            tag = "B-"+multi_token_ent["type"] # TODO: ents after .?
                        else:
                            tag = "I-"+multi_token_ent["type"]
                    else:
                        tag = "O"
                tags.append(tag)
                tupl = (t, offsetFrom, offsetTo, tag)
                tokens.append(tupl)
            
            dict_dataset[sid] = tokens
        
    return dict_dataset

# -- TODO: handle multi-token entities # I think I've done it :D
# tricyclic antidepressants - 'O' should be Group
# chondroitin ABC lyase - 'O' should be drug_n
# heparinase III - 'O' should be drug_n
# hyaluronan lyase - 'O' should be drug_n
# Mercaptopurine/Azathioprine - 'O' should be drug
# muscle relaxants 

In [3]:
path_train = "../../labAHLT/data/train"
path_dev = "../../labAHLT/data/devel"

train_dataset = load_data(path_train)
devel_dataset = load_data(path_dev)

print(train_dataset['DDI-DrugBank.d661.s5'])

[('Interactions', 0, 11, 'O'), ('observed', 23, 30, 'O'), ('nondepolarizing', 43, 57, 'B-group'), ('muscle', 59, 64, 'I-group'), ('relaxants', 66, 74, 'I-group'), ('administered', 86, 97, 'O'), ('succession', 102, 111, 'O'), ('.', 112, 112, 'O')]


In [114]:
def create_index(dataset, max_length):
    '''
    Task: Create index dictionaries both for input (words) and output (labels) from given dataset
    Input: 
        dataset: dataset produced by load_data.
        max_length: maximum length of a sentence (longer sentences will be cut, shorter ones will be padded).
        
    Output: A dictionary where each key is an index name (e.g. "words", "labels"), and the value is a 
            dictionary mapping each word/label to a number. An entry with the value for maxlen is also stored
    Example: 
        >>> create_indx(traindata)
        {'words': {'<PAD>':0, '<UNK>':1, '11-day':2, 'murine':3, 'criteria':4,
                   'stroke':5, ... ,'levodopa':8511, 'terfenadine': 8512}
         'labels': {'<PAD>':0, 'B-group':1, 'B-drug_n':2, 'I-drug_n':3, 'O':4, 
                    'I-group':5, 'B-drug':6, 'I-drug':7, 'B-brand':8, 'I-brand':9}
         'maxlen': 100 }
    '''
    
    index_words = {'<PAD>':0, '<UNK>':1}
    i = 2
    
    index_labels = {'<PAD>':0}
    j = 1
    
    
    
    for key, item in dataset.items():
        for t in item:
            word = t[0].lower() # use lower case words? 
            tag = t[3]
            if word not in index_words:
                index_words[word] = i
                i += 1
            if tag not in index_labels:
                index_labels[tag] = j
                j += 1

    indexs = {'words': index_words, 'labels': index_labels, 'maxlen':max_length}
    
    return indexs    

In [123]:
idx = create_index(train_dataset, 20)
idx['labels']

{'<PAD>': 0,
 'O': 1,
 'B-brand': 2,
 'B-drug': 3,
 'B-group': 4,
 'I-group': 5,
 'I-drug': 6,
 'I-brand': 7,
 'B-drug_n': 8,
 'I-drug_n': 9}

In [221]:
def encode_words(dataset, idx):
    '''
    Task: Encode the words in a sentence dataset formed by lists of tokens into lists of indexes
          suitable for NN input.
    Input: 
        dataset: A dataset produced by load_data.
        idx: A dictionary produced by create_indexs, containing word and label indexes, as well
             as the maximum sentence length.
             
    Output: The dataset encoded as a list of sentence, each of them is a list of word indices.
            If the word is not in the index, <UNK> code is used. If the sentence is shorter than
            max_len it is padded with <PAD> code.
    Example: 
        >>> encode_words(traindata, idx)
            [ [6882 1049 4911 ... 0 0 0 ]
            [  2290 7548 8069 ... 0 0 0 ]
               ...
            [  2002 6582 7518 ... 0 0 0 ] ]
    '''
    max_length = idx['maxlen']
    seq = []
    for key, item in dataset.items():
        aux = []
        for t in item:
            w = str(t[0]).lower() # When using lower case words
            if w in idx['words']:
                i = idx['words'][w]
            else:
                i = idx['words']['<UNK>']
            aux.append(i)
        seq.append(aux)  
    
    seq_padded = pad_sequences(maxlen = max_length, sequences = seq, padding = 'post')
    
    return seq_padded

def encode_labels(dataset, idx):
    '''
    Task: Encode the ground truth labels in a dataset formed by lists of tokens into lists of indexes
        suitable for NN output.
    Input:
        dataset: A dataset produced by load_data.
        idx: A dictionary produced by create_index, containing word and label indexes, as well as the maximum length.
        
    Output: The dataset encoded as a list of sentence, each of them is a list of BIO label indices. If the sentence
            is shorter than max_len it is padded with <PAD> code. 
    
    Example :
     >>> encode_labels ( traindata , idx )
        [[ [4] [6] [4] [4] [4] [4] ... [0] [0] ]
        [  [4] [4] [8] [4] [6] [4] ... [0] [0] ]
          ...
        [
    '''
    max_length = idx['maxlen']
    seq = []
    for key, item in dataset.items():
        aux = []
        for t in item:
            w = t[3]
            i = idx['labels'][w]
            aux.append(i)
        seq.append(aux)
    seq_padded = pad_sequences(maxlen = max_length, sequences = seq, padding = 'post', truncating="post")
    seq_categ = [to_categorical(i, num_classes = 10) for i in seq_padded]  # 9 classes + 1 PAD
    
    return seq_padded, seq_categ

In [222]:
X_train = encode_words(train_dataset, idx)
Y, Y_train = encode_labels(train_dataset, idx)

X_dev = encode_words(devel_dataset, idx)
Ydev, Y_dev = encode_labels(devel_dataset, idx)

In [8]:
print(X_train)

[[   2    3    4 ...    0    0    0]
 [   2   12    3 ...    0    0    0]
 [  19   20   21 ...    0    0    0]
 ...
 [   2  101 3387 ...    0    0    0]
 [1159  910 5135 ...    0    0    0]
 [  19  910 5135 ...    0    0    0]]


In [9]:
print(Y[0])
print(Y_train[0][0:10])

[1 1 2 1 1 3 1 1 3 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
[[0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]]


In [72]:
def build_network(idx):
    '''
    Task: Create network for the learner. 
    Input:
        idx: index dictionary with word/labels codes, plus maximum sentence length.
    Output: Returns a compiled Keras neural network with the specified layers
    '''
    
    #sizes
    n_words = len(idx['words'])
    n_labels = len(idx['labels'])#+1
    max_len = idx['maxlen']
    
    # create network layers
    inp = Input(shape=(max_len,))
    model = Embedding(input_dim=n_words + 1, output_dim = n_labels, input_length = max_len)(inp)
    model = Bidirectional(LSTM(units=512, return_sequences=True, recurrent_dropout=0.2, dropout=0.2))(model)
    model2 = Bidirectional(LSTM(units=512, return_sequences=True,recurrent_dropout=0.2, dropout=0.2))(model)
    model = add([model, model2])
    out = TimeDistributed(Dense(n_labels, activation="softmax"))(model)
    
    # create and compile model
    model = Model(inp, out)
    
#     optimiz = Adam(lr=0.01, decay=1e-6)
    model.compile(optimizer="adam", loss="categorical_crossentropy", metrics=["accuracy"])
    
    return model

In [151]:
def build_network(idx):
    '''
    Task: Create network for the learner. 
    Input:
        idx: index dictionary with word/labels codes, plus maximum sentence length.
    Output: Returns a compiled Keras neural network with the specified layers
    '''
    
    #sizes
    n_words = len(idx['words'])
    n_labels = len(idx['labels'])#+1
    max_len = idx['maxlen']
    
    # create network layers
    inp = Input(shape=(max_len,))
    model = Embedding(input_dim=n_words + 1, output_dim = n_labels, input_length = max_len)(inp)
    model = Dense(32, activation="relu")(model)
    model = Dropout(0.2)(model)
    model = Bidirectional(LSTM(units=100, return_sequences=True, recurrent_dropout=0.2))(model)
#     out = TimeDistributed(Dense(n_labels, activation="softmax"))(model)
    out = Dense(n_labels, activation="softmax")(model)
    
    # create and compile model
    model = Model(inp, out)
    
#     optimiz = Adam(lr=0.01, decay=1e-6)
    model.compile(optimizer="adam", loss="categorical_crossentropy", metrics=["accuracy"])
    
    return model

In [152]:
model = build_network(idx)
model.summary()

Model: "model_23"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_25 (InputLayer)        [(None, 20)]              0         
_________________________________________________________________
embedding_24 (Embedding)     (None, 20, 10)            83050     
_________________________________________________________________
dense_32 (Dense)             (None, 20, 32)            352       
_________________________________________________________________
dropout_23 (Dropout)         (None, 20, 32)            0         
_________________________________________________________________
bidirectional_24 (Bidirectio (None, 20, 200)           106400    
_________________________________________________________________
dense_33 (Dense)             (None, 20, 10)            2010      
Total params: 191,812
Trainable params: 191,812
Non-trainable params: 0
____________________________________________________

In [153]:
history = model.fit(X_train, np.array(Y_train),
                   batch_size=32,
                   epochs=2,
                   verbose=1, 
                   validation_data=(X_dev, np.array(Y_dev)))

Epoch 1/2
170/170 [==============================] - 10s 29ms/step - loss: 1.2375 - accuracy: 0.6545 - val_loss: 0.3862 - val_accuracy: 0.8826
Epoch 2/2
170/170 [==============================] - 3s 20ms/step - loss: 0.3193 - accuracy: 0.9011 - val_loss: 0.2683 - val_accuracy: 0.9151


In [143]:
def save_model_and_indexes(model, idx):#, filename):
    '''
    Task: Save given model and indexs to disk
    Input: 
        model: Keras model created by _build_network, and trained.
        idx: A dictionary produced by create_indexs, containing word and label indexes, 
             as well as the maximum sentence length. 
        filename: Saves the mode into filename.nn and the indexes into filename.idx
    '''
    model.save("ner-nn.nn")
    
    file = open("index_ner.pkl", "wb")
    pickle.dump(idx, file)
    file.close()

## `Learner()`

In [223]:
def learner(traindir, validationdir):#, modelname):
    '''
    Learns a NN model using traindir as training data, and validationdir as validation data.
    Saves learnt model in a file named modelname
    '''
    # load train and validation data in a suitable form
    train_dataset = load_data(traindir)
    val_dataset = load_data(validationdir)
    
    # create indexes from trainindg data 
    max_len = 20
    idx = create_index(train_dataset, max_len)
    
    # build network 
    model = build_network(idx)
    
    # encode datasets
    Xtrain = encode_words(train_dataset, idx)
    Y, Ytrain = encode_labels(train_dataset, idx)
    Xval = encode_words(val_dataset, idx)
    Yv, Yval = encode_labels(val_dataset, idx)
    
    # train model
    model.fit(Xtrain, np.array(Ytrain),
              batch_size=32,
              epochs=2,
              verbose=1,
              validation_data=(Xval, np.array(Yval)))
    
    # save model and indexs, for later use in prediction
    save_model_and_indexes(model, idx)#, path_dev.split('/')[-1]+"NER-learned")

In [224]:
path_train = "../../labAHLT/data/train"
path_dev = "../../labAHLT/data/devel"
learner(path_train, path_dev)

Epoch 1/2
170/170 [==============================] - 11s 33ms/step - loss: 1.2287 - accuracy: 0.6697 - val_loss: 0.4457 - val_accuracy: 0.8820
Epoch 2/2
170/170 [==============================] - 4s 24ms/step - loss: 0.4084 - accuracy: 0.8851 - val_loss: 0.3502 - val_accuracy: 0.8999
INFO:tensorflow:Assets written to: ner-nn.nn/assets


***
## Functions Classifier

In [225]:
def load_model_and_indexs():
    '''
    Task: Load model and associate indexs from disk.
    Input:
        filename: filename to be loaded
    Output: Loads a model from filename.nn and its indexes from filename.idx
            Returns the loaded model and indexes. 
    '''
    model = load_model("ner-nn.nn")
    index = open("index_ner.pkl", "rb")
    idx = pickle.load(index)
    
    return model, idx

In [240]:
def output_entities(dataset, preds, outfile):
    '''
    Task: Output detected entities in the format expected by the evaluator
    Input: 
        dataset: A dataset produced by load_data.
        preds: For each sentence in dataset, a list with the labels for each sentence token, 
               as predicted by the model.
    Output: prints the detected entities to stdout in the format required by the evaluator. 
    '''
    outf = open(outfile, 'w')
    for sentence, pred in zip(dataset.items(), preds):
#         print(sentence, pred)
        sid = sentence[0]
        tokens = sentence[1]
        for i in range(min(len(tokens), len(pred))):
            token = tokens[i]
            label = pred[i]
            if label[0] == 'B':
                offset_from = str(token[1])
                offset_to = str(token[2])
                tag_name = label[2:]
                entity = token[0]
                j = i+1
                while j < len(tokens) and len(tokens[j]) >=3:
                    token_next = tokens[j]
                    word_next = token_next[0]
                    offset_from_next = str(token_next[1])
                    offset_to_next = str(token_next[2])
                    tag_next = pred[j]
                    j += 1
                    if int(offset_from_next) - int(offset_to) != 2 or tag_next[0] != 'I':
                        break
                    if tag_next[2:] == tag_name:
                        entity = entity + ' ' + word_next
                        offset_to = offset_to_next
                outf.write(sid + "|" + offset_from + '-' + offset_to + "|" + entity + "|" + tag_name+'\n')
                print(sid + "|" + offset_from + '-' + offset_to + "|" + entity + "|" + tag_name)

In [241]:
Y_pred = model.predict(X_dev)
Y = np.argmax(Y_pred, axis=-1)
# for y in Y_pred:
#     for s in y:
#         print(s)
#         print(np.argmax(s))
key_list = list(idx['labels'].keys())
val_list = list(idx['labels'].values())
for y in Y:
    for t in y:
        if t in [3,4,5,6,7,8,9]: 
            print(key_list[t])
        break

[4.2584034e-06 9.9451423e-01 7.0119504e-04 6.3965784e-04 6.8987219e-04
 2.1726682e-03 3.5083498e-04 2.0660178e-04 4.4540118e-04 2.7531656e-04]
1
[3.77198041e-04 1.19248092e-01 6.32151738e-02 3.91709924e-01
 1.68281049e-01 7.66557455e-02 1.14880666e-01 1.91415939e-02
 3.07506043e-02 1.57399159e-02]
3
[2.8591698e-05 9.5812088e-01 6.0878699e-03 7.6709664e-03 4.7152555e-03
 1.1617368e-02 5.0736773e-03 1.7525057e-03 3.2359639e-03 1.6969464e-03]
1
[1.9761694e-05 9.6455818e-01 6.1134631e-03 7.0058485e-03 3.0764707e-03
 8.2032643e-03 5.3358027e-03 1.5894885e-03 2.7867407e-03 1.3110423e-03]
1
[3.2601744e-07 9.9964583e-01 7.9186779e-05 2.5364998e-05 1.8289580e-05
 1.2798521e-04 3.0788011e-05 1.8768729e-05 3.3944190e-05 1.9516727e-05]
1
[1.9955465e-05 9.7700149e-01 4.6447790e-03 4.5927325e-03 2.0487835e-03
 4.1285544e-03 3.9140815e-03 9.9247310e-04 1.7630686e-03 8.9411257e-04]
1
[1.2558105e-06 9.9910492e-01 2.0340126e-04 8.6972934e-05 5.9128030e-05
 2.7022770e-04 9.5828669e-05 4.6280620e-05 8.077

 2.6171119e-05 3.8542735e-06 4.6131350e-07 2.3274653e-07 4.2099117e-07]
0
[9.9991894e-01 1.2713214e-06 4.4798909e-07 2.5103542e-05 1.3230227e-05
 3.3653494e-05 5.6121694e-06 7.0439410e-07 3.2945027e-07 6.2630454e-07]
0
[9.9987495e-01 1.7320730e-06 7.3099545e-07 3.5618639e-05 2.0911717e-05
 5.3153519e-05 1.0038395e-05 1.3053854e-06 5.6581513e-07 1.1165872e-06]
0
[9.9977046e-01 2.6790349e-06 1.3840676e-06 6.1037208e-05 3.9379356e-05
 9.8228331e-05 2.0808537e-05 2.7560536e-06 1.1140221e-06 2.2490499e-06]
0
[9.9953783e-01 4.5078327e-06 2.8276474e-06 1.1732031e-04 8.1577557e-05
 1.9668583e-04 4.5976692e-05 6.1231499e-06 2.3296375e-06 4.7576118e-06]
0
[9.9906665e-01 7.9010770e-06 5.7900638e-06 2.3016834e-04 1.6905335e-04
 3.9323367e-04 9.9391480e-05 1.3281095e-05 4.7923463e-06 9.8540213e-06]
0
[1.9666721e-04 7.3182571e-01 3.0549889e-02 7.7213421e-02 6.1028905e-02
 6.0196675e-02 1.1017428e-02 5.8245100e-03 1.4869370e-02 7.2773648e-03]
1
[0.00067135 0.2741002  0.07636645 0.32665858 0.14372046 

 8.3537445e-05 3.2272288e-05 1.3456467e-05 1.6534257e-05 1.1333415e-05]
1
[5.1390834e-06 9.9890459e-01 2.2189220e-04 7.2926647e-05 4.0544179e-05
 2.9287898e-04 2.2926442e-04 7.5458309e-05 9.2179034e-05 6.5114364e-05]
1
[2.7621170e-06 9.9991381e-01 2.2155184e-05 2.2982897e-06 2.1084500e-06
 2.1519278e-05 9.4914949e-06 9.4393554e-06 7.7422201e-06 8.7105254e-06]
1
[1.0555682e-06 9.9684000e-01 4.9140782e-04 2.6280497e-04 1.9876740e-04
 1.2455230e-03 3.3149659e-04 1.7673564e-04 3.0336517e-04 1.4893083e-04]
1
[2.9991980e-07 9.9946588e-01 9.5313495e-05 3.5425132e-05 3.2614345e-05
 1.9822875e-04 4.9882747e-05 3.3556193e-05 5.5112847e-05 3.3638826e-05]
1
[3.28406968e-05 9.18785572e-01 1.23444768e-02 1.69376507e-02
 7.64096482e-03 1.26092285e-02 1.84670202e-02 4.16936539e-03
 6.02573808e-03 2.98710144e-03]
1
[1.3920817e-07 9.9979204e-01 4.2510732e-05 1.0518763e-05 9.0813446e-06
 7.6498814e-05 2.2105467e-05 1.4033065e-05 1.9399104e-05 1.3558278e-05]
1
[7.75195190e-07 9.99154806e-01 1.72694272e-04

 0.07675998 0.01437595 0.0221824  0.0165228 ]
1
[0.00208048 0.01531984 0.03083045 0.53476983 0.18343398 0.07530021
 0.12383915 0.01017365 0.01541482 0.00883762]
3
[0.00191209 0.18347728 0.04066445 0.33099133 0.09979407 0.17557196
 0.1211876  0.0137433  0.02195607 0.01070193]
3
[2.8655189e-05 9.9299556e-01 5.8721291e-04 8.1005518e-04 5.1123509e-04
 3.7647665e-03 4.8043113e-04 2.2335176e-04 3.5953059e-04 2.3919770e-04]
1
[0.00491039 0.0331912  0.03422046 0.5306998  0.16190572 0.09024455
 0.10982909 0.00997059 0.01622912 0.00879905]
3
[0.00679156 0.3332188  0.04057743 0.26220417 0.06578361 0.16770716
 0.08571557 0.01117379 0.01863212 0.00819574]
1
[1.72057426e-05 9.99791086e-01 2.94109614e-05 1.16732281e-05
 6.86325302e-06 9.86576269e-05 1.18885437e-05 1.12091639e-05
 1.37268535e-05 8.37999778e-06]
1
[9.9320084e-01 8.3124399e-04 3.2830136e-04 1.8392019e-03 8.5191894e-04
 9.4497745e-04 1.3869646e-03 1.9009308e-04 1.9815720e-04 2.2837135e-04]
0
[9.9690348e-01 1.3764156e-04 8.5296422e-05 7.9

 9.5249899e-04 1.1904018e-04 1.7671298e-05 1.7142120e-05 1.5821292e-05]
0
[9.9871230e-01 1.7767306e-05 7.4438753e-06 6.6829647e-04 2.0826586e-04
 3.3646915e-04 3.6798461e-05 4.7398485e-06 3.8803314e-06 4.1282792e-06]
0
[9.9951267e-01 6.3954189e-06 2.3137020e-06 2.4376092e-04 7.6083517e-05
 1.3979974e-04 1.4431898e-05 1.6948160e-06 1.2224427e-06 1.4809175e-06]
0
[9.9977583e-01 3.0802807e-06 9.7752343e-07 1.0633274e-04 3.4511871e-05
 6.9808113e-05 7.2458806e-06 8.0902549e-07 5.3204485e-07 7.1943941e-07]
0
[9.9987602e-01 1.8568402e-06 5.3621216e-07 5.5027827e-05 1.9122408e-05
 4.1690611e-05 4.5463512e-06 4.9966360e-07 3.0565039e-07 4.5232807e-07]
0
[9.9991775e-01 1.3338994e-06 3.6877046e-07 3.3700377e-05 1.2798395e-05
 2.9613828e-05 3.4950212e-06 3.8884971e-07 2.2302602e-07 3.5571207e-07]
0
[9.9993408e-01 1.1201217e-06 3.1470287e-07 2.4726369e-05 1.0404983e-05
 2.5190186e-05 3.2873704e-06 3.7817250e-07 2.0331267e-07 3.4600882e-07]
0
[9.99934793e-01 1.10275244e-06 3.35339820e-07 2.22687249

...

 2.02575338e-05 1.05705039e-05]
1
[3.3645813e-06 9.9457234e-01 1.2446811e-03 7.2524376e-04 2.7731195e-04
 9.3102537e-04 1.2121334e-03 3.3936248e-04 4.7499413e-04 2.1958594e-04]
1
[2.2370452e-07 9.9970526e-01 7.9379759e-05 2.0195610e-05 9.5124942e-06
 7.5658427e-05 4.5067121e-05 2.0896965e-05 2.8729410e-05 1.5052264e-05]
1
[3.9565251e-07 9.9953055e-01 1.3222396e-04 3.7082718e-05 1.6140175e-05
 1.0100596e-04 8.3060433e-05 3.2249565e-05 4.3990647e-05 2.3167850e-05]
1
[2.6632566e-07 9.9972349e-01 8.1351303e-05 1.9629948e-05 8.8200168e-06
 6.1898667e-05 4.5752826e-05 1.8818422e-05 2.5620328e-05 1.4279375e-05]
1
[3.0465193e-07 9.9974161e-01 7.7400276e-05 1.8287494e-05 8.6068812e-06
 5.7601505e-05 4.2304884e-05 1.6908232e-05 2.3399120e-05 1.3724237e-05]
1
[4.4583021e-07 9.9969161e-01 9.3171366e-05 2.3009818e-05 1.1256090e-05
 6.6913519e-05 5.1283434e-05 1.9417570e-05 2.6717933e-05 1.6353324e-05]
1
[2.6932298e-07 9.9987137e-01 3.8869341e-05 8.2505276e-06 5.1239631e-06
 3.3008910e-05 1.6365189e

 1.18409465e-04 4.89943195e-05]
1
[2.6391834e-07 9.9975282e-01 8.7350214e-05 2.1857826e-05 1.1974189e-05
 6.1910578e-05 1.7517557e-05 1.0911288e-05 2.4608555e-05 1.0832024e-05]
1
[1.3604752e-06 9.9924266e-01 2.8446069e-04 1.0149793e-04 4.5256398e-05
 1.5496406e-04 5.4547530e-05 2.8291250e-05 6.1330022e-05 2.5580133e-05]
1
[1.1066409e-06 9.9996042e-01 1.4814926e-05 4.4012731e-06 2.0364882e-06
 9.6512395e-06 1.7834074e-06 1.6007629e-06 2.6340520e-06 1.4956066e-06]
1
[9.5334822e-01 3.3896433e-03 1.9434803e-03 2.8520355e-02 6.2714959e-03
 2.1328107e-03 3.0365796e-03 3.9247438e-04 5.3074444e-04 4.3418229e-04]
0
[9.9153179e-01 3.0400997e-04 1.8643241e-04 4.9225646e-03 1.2779015e-03
 1.0581079e-03 5.3295452e-04 6.2593237e-05 6.6160886e-05 5.7533623e-05]
0
[9.97973502e-01 4.37420349e-05 2.39265446e-05 1.10091339e-03
 3.11022741e-04 4.07350832e-04 1.08439686e-04 1.14703962e-05
 9.66505922e-06 9.94182665e-06]
0
[9.9936444e-01 1.0611514e-05 4.7698422e-06 3.2053946e-04 9.6685253e-05
 1.6609239e-04

 1.3843382e-03 1.1156346e-03 3.8974805e-04 5.2060676e-04 2.9279495e-04]
1
[3.10532101e-07 9.99678731e-01 6.07859583e-05 1.98134949e-05
 1.63182467e-05 1.07362226e-04 4.02256810e-05 2.29630023e-05
 3.03904435e-05 2.31129961e-05]
1
[2.0139593e-04 7.6642674e-01 2.4827061e-02 6.0214479e-02 2.4862712e-02
 2.7528813e-02 6.6617288e-02 9.8494794e-03 1.2279667e-02 7.1924767e-03]
1
[1.0214618e-05 9.9230015e-01 1.0210689e-03 8.7791850e-04 5.5041153e-04
 2.2811356e-03 1.4930984e-03 4.7946349e-04 5.8389944e-04 4.0261846e-04]
1
[1.5129027e-04 8.6530417e-01 1.3221148e-02 2.9852182e-02 1.1246156e-02
 2.3976563e-02 3.7825130e-02 6.2993863e-03 7.6951394e-03 4.4288719e-03]
1
[5.8749065e-06 9.9369264e-01 8.4045995e-04 6.7596935e-04 3.0908757e-04
 1.9893269e-03 1.3031284e-03 4.0009010e-04 4.8282085e-04 3.0057036e-04]
1
[5.6282477e-07 9.9961519e-01 6.0081467e-05 2.4381858e-05 1.8565552e-05
 1.4737117e-04 5.0021503e-05 2.5808898e-05 3.1393149e-05 2.6652220e-05]
1
[3.0212925e-04 8.0958802e-01 1.7452886e-02 5.

 8.2382131e-03 3.3899492e-03 1.4029050e-03 3.2252495e-03 1.5936600e-03]
1
[8.1347018e-05 8.9027274e-01 1.7529694e-02 3.3816651e-02 1.5486644e-02
 1.7757805e-02 1.0795327e-02 3.1600569e-03 7.6423991e-03 3.4572943e-03]
1
[8.7648616e-05 8.7259632e-01 2.2474056e-02 4.1358687e-02 1.2665236e-02
 1.8842150e-02 1.6228341e-02 3.7417109e-03 8.7052621e-03 3.3005027e-03]
1
[5.2444483e-07 9.9951410e-01 1.4274158e-04 4.5073801e-05 2.3484527e-05
 1.5031536e-04 3.5467241e-05 2.1071179e-05 4.6981037e-05 2.0169751e-05]
1
[7.9884973e-07 9.9956280e-01 1.5335584e-04 5.0017159e-05 2.3154327e-05
 1.0974605e-04 2.9421664e-05 1.7507597e-05 3.7185622e-05 1.5909502e-05]
1
[1.1038392e-06 9.9996233e-01 1.3658292e-05 4.0307200e-06 1.8859058e-06
 9.6379490e-06 1.6959715e-06 1.5737421e-06 2.5697186e-06 1.4435631e-06]
1
[9.6359146e-01 3.0212910e-03 1.5918976e-03 2.1332050e-02 4.8785419e-03
 1.8494418e-03 2.5708785e-03 3.3590972e-04 4.5202585e-04 3.7661457e-04]
0
[9.9363530e-01 2.6430059e-04 1.4852072e-04 3.5213975e-03

[0.02373114 0.00579494 0.01446745 0.46481463 0.15707634 0.16752174
 0.14166322 0.00894215 0.00918709 0.00680132]
3
[0.02697927 0.01624522 0.01768952 0.41068098 0.09651008 0.23097038
 0.1724293  0.0106747  0.01111148 0.00670912]
3
[2.02350653e-04 9.96671379e-01 1.47154409e-04 1.09300505e-04
 6.97564610e-05 2.30953656e-03 1.65362755e-04 1.19785931e-04
 1.19848097e-04 8.55416874e-05]
1
[1.1682286e-06 9.9774301e-01 4.6812062e-04 2.2936611e-04 1.5547879e-04
 8.3507854e-04 1.7151586e-04 9.2324372e-05 2.1226173e-04 9.1649417e-05]
1
[8.17948433e-07 9.98821557e-01 2.77916231e-04 1.25866965e-04
 8.89206785e-05 3.53265990e-04 9.38157391e-05 5.68443575e-05
 1.20046294e-04 6.08332521e-05]
1
[4.2645232e-05 9.2644775e-01 1.3980214e-02 2.0251170e-02 7.7002835e-03
 1.0210537e-02 1.0904095e-02 2.6355430e-03 5.4231449e-03 2.4046958e-03]
1
[3.6054435e-06 9.9414355e-01 1.5209952e-03 8.9827942e-04 3.5929360e-04
 1.2225929e-03 7.9474534e-04 2.7488475e-04 5.4838654e-04 2.3382934e-04]
1
[1.4380012e-07 9.998457

## `Classifier()`

In [242]:
def predict(datadir, outfile):
    '''
    Loads a NN model from a file 'modelname' and uses it to extract drugs in datadir. Saves
    results to 'outfile' in the appropriate format
    '''
    
    # load model and associated encoding data
    model, idx = load_model_and_indexs()
    
    # load data to annotate
    testdata = load_data(datadir)
#     print(idx)
    
    # encode dataset
    X = encode_words(testdata, idx)
    
    # tag sentences in dataset
    Y = model.predict(X)
    Y = [[find_label(idx, np.argmax(y)) for y in s] for s in Y]
    
    # extract entities and dump them to output file
    output_entities(testdata, Y, outfile)
    
    # evaluate using official evaluator
    evaluate("NER", datadir, outfile)

In [243]:
def find_label(idx, predicted):
    for label, i in idx["labels"].items():
        if i == predicted:
            return label

In [244]:
path_test = "../../labAHLT/data/test"
predict(path_test, "NER-result2")

DDI-DrugBank.d485.s0|0-6|Ethinyl|drug
DDI-DrugBank.d485.s0|8-16|estradiol|drug
DDI-DrugBank.d485.s2|0-12|Acetaminophen|drug
DDI-DrugBank.d485.s3|21-34|contraceptives|drug
DDI-DrugBank.d485.s3|82-94|acetaminophen|drug
DDI-DrugBank.d485.s4|0-8|Acitretin|drug
DDI-DrugBank.d485.s5|35-48|contraceptives|drug
DDI-DrugBank.d485.s6|0-16|Aminoglutethimide|drug
DDI-DrugBank.d485.s10|0-13|Anticoagulants|drug
DDI-DrugBank.d485.s10|37-50|contraceptives|drug
DDI-DrugBank.d485.s10|92-99|coumarin|drug
DDI-DrugBank.d485.s10|101-111|derivatives|drug
DDI-DrugBank.d485.s11|21-34|contraceptives|drug
DDI-DrugBank.d485.s12|0-14|Anticonvulsants|drug
DDI-DrugBank.d485.s12|17-29|carbamazepine|drug
DDI-DrugBank.d485.s12|43-55|phenobarbital|drug
DDI-DrugBank.d485.s12|58-66|phenytoin|drug
DDI-DrugBank.d485.s12|109-115|ethinyl|drug
DDI-DrugBank.d485.s12|117-125|estradiol|drug
DDI-DrugBank.d485.s16|0-11|Atorvastatin|drug
DDI-DrugBank.d485.s16|0-11|Atorvastatin|drug
DDI-DrugBank.d485.s16|67-73|ethinyl|drug
DDI-DrugBan

Ignoring duplicated entity in system predictions file: DDI-DrugBank.d485.s16|0-11|Atorvastatin|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d485.s23|0-11|Griseofulvin|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d485.s36|0-7|Rifampin|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d485.s43|62-69|caffeine|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d480.s10|22-32|epinephrine|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d480.s15|47-55|Clozapine|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d480.s18|42-54|carbamazepine|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d480.s22|84-92|clozapine|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d337.s1|18-27|Inhibitors|drug
Ignoring duplicated entity in system predictions file: DDI-DrugBank.d337.s1|0-6|HMG-CoA|drug
Ignoring duplicated

In [ ]:
model, idx = load_model_and_indexs()
testdata = load_data(path_test)
X = encode_words(testdata, idx)
Y = model.predict(X)